# House Price Predictions

## Introduction

In this notebook, we will look at the house prices dataset and try to fit a ordinary least squares model with cross validation. At the end we will use that model to predict the house prices from a test dataset.

### Imports

In [1]:
import numpy as np
import pandas as pd
import os
from pandas.tseries.offsets import MonthEnd
import statsmodels.formula.api as sm
from IPython.display import display
from plotly import tools
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
import warnings
warnings.simplefilter('ignore')

### Parameter and Function Definitions

In [2]:
data_path = 'data'
train_data_path = os.path.join(data_path, 'train.csv')
test_data_path = os.path.join(data_path, 'test.csv')

output_path = os.path.join('output', 'test.csv')

old_predict_column = 'SalePrice'
new_predict_column = 'sale_price'
predict_column = 'log_sale_price'

rename_columns = {
    'PropertyID': 'property_id', 
    'SaleDate': 'sale_date', 
    'Town': 'town', 
    'Bedrooms': 'bedrooms', 
    'Bathroom': 'bathroom',
    'PropertyType': 'property_type', 
    'DistanceFromCBD': 'distance_from_cbd', 
    'CarSpaces': 'car_spaces', 
    'Gardensqm': 'garden_sqm', 
    'Landsqm': 'land_sqm',
    'floorsqm': 'floor_sqm', 
    'YearBuilt': 'year_built', 
    'Region': 'region', 
    'TownDensity': 'town_density', 
    old_predict_column: new_predict_column
}

category_columns = ['town', 'region', 'property_type']

def get_data(path):
    return pd.read_csv(path, index_col=0, dayfirst=True, parse_dates=['SaleDate'])

def make_histogram_figure(data, title):
    return go.Figure([go.Histogram(x=data)], layout=go.Layout(title=title))

def clean_data(df, rename_columns, category_columns, log_columns):
    
    clean_df = df.copy()
    
    clean_df = clean_df.rename(columns=rename_columns)
    
    clean_df[category_columns] = clean_df[category_columns].astype('category')
    
    try:
        clean_df[[f'log_{item}' for item in log_columns]] = np.log(clean_df[log_columns])
    except KeyError:
        print('No columns to fit.')
    
    clean_df['year'] = clean_df['sale_date'].dt.year
    clean_df['month'] = clean_df['sale_date'].dt.month
    clean_df['year_month'] = clean_df['sale_date'] + MonthEnd(1)
    
    return clean_df

## Raw Data

In [3]:
raw_df = get_data(train_data_path)
display(raw_df.columns)
display(raw_df.describe())
display(raw_df['Town'].unique())
display(raw_df['PropertyType'].unique())
display(raw_df['Region'].unique())
display(raw_df.head())

Index(['PropertyID', 'SaleDate', 'Town', 'Bedrooms', 'Bathroom',
       'PropertyType', 'DistanceFromCBD', 'CarSpaces', 'Gardensqm', 'Landsqm',
       'floorsqm', 'YearBuilt', 'Region', 'TownDensity', 'SalePrice'],
      dtype='object')

PropertyID     Bedrooms     Bathroom  DistanceFromCBD    CarSpaces  \
count  7700.000000  7700.000000  5788.000000      7700.000000  5694.000000   
mean   4837.816623     2.848961     1.544921         8.200779     1.639269   
std    2782.105988     0.991413     0.734181         3.211158     0.977982   
min       0.000000     1.000000     0.000000         2.400000     0.000000   
25%    2421.750000     2.000000     1.000000         5.500000     1.000000   
50%    4865.500000     3.000000     1.000000         7.900000     2.000000   
75%    7257.250000     3.000000     2.000000        11.200000     2.000000   
max    9623.000000    12.000000     8.000000        13.900000    10.000000   

         Gardensqm       Landsqm     floorsqm    YearBuilt   TownDensity  \
count  2927.000000   5162.000000  2927.000000  3381.000000   7700.000000   
mean    146.525624    501.405076   146.525624  1958.977226  10715.610260   
std     108.032741   1470.462547   108.032741    38.359122   4146.151896   
min       0.000000      0.000000     0.000000  1850.000000   3578.000000   
25%      90.000000    174.000000    90.000000  1930.000000   7809.000000   
50%     123.000000    393.000000   123.000000  1960.000000  10331.000000   
75%     177.000000    633.000000   177.000000  1997.000000  11918.000000   
max    3112.000000  75100.000000  3112.000000  2019.000000  21650.000000   

          SalePrice  
count  7.700000e+03  
mean   1.181539e+06  
std    7.307287e+05  
min    8.500000e+04  
25%    6.788098e+05  
50%    9.900000e+05  
75%    1.490000e+06  
max    1.120000e+07

array(['Surrey Hills', 'Wapping', 'Kellyville', 'Hillbrow', 'Denver',
       'Chiswick', 'Abbotsford', 'Fairfield', 'Enfield', 'Darlington',
       'Greenwich', 'Carlingford', 'Haberfield', 'Leichhardt', 'Malabar',
       'Heckenberg', 'Kings Park', 'Liverpool', 'Osbourne Park',
       'Oyster Bay', 'Penrith', 'Tempe', 'Preston', 'Newcastle',
       'Pennant Hills', 'Waverly', 'Denistone', 'Double Bay',
       'Chester Hill', 'Chipping Norton', 'Granville'], dtype=object)

array(['House', 'Terrace', 'Flat'], dtype=object)

array(['ZoneA', 'ZoneB', 'ZoneC'], dtype=object)

PropertyID   SaleDate          Town  Bedrooms  Bathroom PropertyType  \
0        3826 2016-06-27  Surrey Hills         3       1.0        House   
1        6979 2017-09-23       Wapping         2       1.0        House   
2        7290 2017-10-07    Kellyville         1       NaN      Terrace   
3        7254 2017-10-07      Hillbrow         2       NaN         Flat   
4        8407 2017-11-25        Denver         2       1.0      Terrace   

   DistanceFromCBD  CarSpaces  Gardensqm  Landsqm  floorsqm  YearBuilt Region  \
0              2.6        2.0        NaN    248.0       NaN        NaN  ZoneA   
1              5.4        0.0       88.0    284.0      88.0     1920.0  ZoneB   
2             12.0        NaN        NaN      NaN       NaN        NaN  ZoneA   
3              5.3        NaN        NaN      NaN       NaN        NaN  ZoneB   
4              6.3        2.0      107.0      NaN     107.0     2001.0  ZoneC   

   TownDensity  SalePrice  
0      14949.0  1570000.0  
1      10331.0  1630000.0  
2      21650.0   405000.0  
3      11308.0   490000.0  
4       6543.0   807000.0

## Price Data Distribution

Below we first see the distribution of the house prices and we find that it looks like a log normal distribution. Therefore we then log the prices and find that the distribution is much more normal.

For ordinary least squares regression, one of the assumptions is that the error terms are normally distributed. This means that we want the error terms to be normally distributed and this happens when the indepedent and dependent variables are normally distributed.

There we will try to predict the log of the house prices instead of the house prices.

In [4]:
iplot(make_histogram_figure(data=raw_df[old_predict_column], title='Sale Prices Histogram'))
iplot(make_histogram_figure(data=np.log(raw_df[old_predict_column]), title='Log Sale Prices Histogram'))

## Clean Data

Here we pythonise column names, make certain column types categorical and get the log of the house prices.

There are one big point to note here which is that a few variables have a lot of missing data. There are two choices to be made here:
- We ignore these variables for the model.
- We try to fill the missing values but if there are too many missing values then this can be hard.

In our case we will ignore these variables.

We add the year and month of the sale date to our data set to check for two things. We check for house price appreciation using the year variable and we check for seasonality using month variable.

In [5]:
clean_df = clean_data(df=raw_df, 
                      rename_columns=rename_columns, 
                      category_columns=category_columns, 
                      log_columns=[new_predict_column])
display(clean_df.describe())

property_id     bedrooms     bathroom  distance_from_cbd   car_spaces  \
count  7700.000000  7700.000000  5788.000000        7700.000000  5694.000000   
mean   4837.816623     2.848961     1.544921           8.200779     1.639269   
std    2782.105988     0.991413     0.734181           3.211158     0.977982   
min       0.000000     1.000000     0.000000           2.400000     0.000000   
25%    2421.750000     2.000000     1.000000           5.500000     1.000000   
50%    4865.500000     3.000000     1.000000           7.900000     2.000000   
75%    7257.250000     3.000000     2.000000          11.200000     2.000000   
max    9623.000000    12.000000     8.000000          13.900000    10.000000   

        garden_sqm      land_sqm    floor_sqm   year_built  town_density  \
count  2927.000000   5162.000000  2927.000000  3381.000000   7700.000000   
mean    146.525624    501.405076   146.525624  1958.977226  10715.610260   
std     108.032741   1470.462547   108.032741    38.359122   4146.151896   
min       0.000000      0.000000     0.000000  1850.000000   3578.000000   
25%      90.000000    174.000000    90.000000  1930.000000   7809.000000   
50%     123.000000    393.000000   123.000000  1960.000000  10331.000000   
75%     177.000000    633.000000   177.000000  1997.000000  11918.000000   
max    3112.000000  75100.000000  3112.000000  2019.000000  21650.000000   

         sale_price  log_sale_price         year        month  
count  7.700000e+03     7700.000000  7700.000000  7700.000000  
mean   1.181539e+06       13.821769  2016.714545     7.142468  
std    7.307287e+05        0.563965     0.646769     3.131833  
min    8.500000e+04       11.350407  2016.000000     1.000000  
25%    6.788098e+05       13.428096  2016.000000     5.000000  
50%    9.900000e+05       13.805460  2017.000000     7.000000  
75%    1.490000e+06       14.214287  2017.000000    10.000000  
max    1.120000e+07       16.231424  2018.000000    12.000000

## Visualise the Data

For each variable we are looking for the following:
- Check if the independent variable is distributed normally.
- Check for a linear relationship.
- Check for a clear trend between the independent and dependent variable.
- Check that there isn't abnormal data distribution with a lot of data or no data for specific values.

We do this by plotting the count for each independent variable to visualise the distribution. We look at the box plots for each independent variables to get an idea for the relationship with the dependent variable.

We use interactive plots so we can have a closer look for certain variables. The distributions are in the translucent blue bars with axis on the left and the box plots represent aggregation for each level for each variable with axis on the right.

In [6]:
def get_box_by_group(df, group_column, predict_column=predict_column):
    return go.Box(y=df[predict_column], name=str(df[group_column].iloc[0]), yaxis='y2', boxmean=True, showlegend=False)

def get_traces_for_feature(df, group_column, predict_column=predict_column):
    
    group_df = df[[group_column, predict_column]].groupby(group_column)
    
    box_traces =  group_df \
        .apply(lambda x: get_box_by_group(x, group_column=group_column)) \
        .tolist()
    
    count_df = group_df.count()
    count_traces = [go.Bar(
        x = count_df.index,
        y = count_df[predict_column],
        name='count-left',
        opacity=0.4,
    )]
    
    traces = count_traces + box_traces
    
    layout = go.Layout(
        title=group_column,
        yaxis=dict(
            title='count',
            showgrid=False,
        ),
        yaxis2=dict(
            title='box_plot - log_sale_price',
            overlaying='y',
            side='right'
        ),
    )
    
    fig = go.Figure(data=traces, layout=layout)

    iplot(fig)
    
view_columns = ['sale_date', 'year_month', 'year', 'month', 'town', 'bedrooms', 'bathroom', 'property_type', 
                'distance_from_cbd', 'car_spaces', 'garden_sqm', 'land_sqm', 'floor_sqm', 'year_built', 'region', 
                'town_density']
for column in view_columns:
    get_traces_for_feature(df=clean_df, group_column=column, predict_column=predict_column)

## Visualise Correlations

In [7]:
corr_df = clean_df.corr()
corr_df = corr_df.loc[corr_df.columns, corr_df.columns]

corr_df = corr_df.reindex(index=corr_df.index[::-1])
trace = go.Heatmap(z=corr_df,
                   x=corr_df.index,
                   y=corr_df.columns)
iplot([trace])

## Data Summary

- Sale date/year/month: We found that there is not a strong relationship between this and the house prices.
- Town: It looks like there are some differences in the box plots meaning that we could use this in the model but it is not clear if there is a continous relationship such as if two towns are close to each other than they should have similar house prices. We could potentially use region information to check this.
- Bedrooms: This has a clear strong relationship with the house prices as you would expect and the data seems normally distributed.
- Bathroom: This looks to have a relationship with the house prices but does not seem normally distributed. If we were to use this, we might do a similar transform that we did to house prices. This has a strong correlation to bedrooms so it might not add much value by using this variable.
- Property Type: This seems to have a relationship with the house prices as you would expect. There are only three values so hard to talk about distribution.
- Distance from CBD: Looks very noisy with a non normal distribution. This seems to be highly correlated with bathrooms which is probably a bogus correlation as this should be true with bedrooms too if it was because that as we got further away from CBD that we got bigger houses.
- Car Spaces: This looks to have relationship with the house prices and looks like a distribution close to normal.
- Garden/Floor/Land Sqm: These data seem to have a strong relationship with the house prices however there are some odd points such as land sqm seems to have a lot of 0 data points. The distribution of the data looks to be log normal, therefore if we wanted to use this, we might log the data. There seem to be some outliers in this data that we would need to take care off if we wanted to use this data. Garden and land sqm are fully correlated which gives us less confidence in this data.
- Year Built: Noisy data.
- Region: There does not seem to be a strong relationship with house prices.
- Town Density: The data looks quite noisy with no relationship with house prices.

## Model

To build our model, we will choose the variables which look to have a strong relationship, do not have any missing values and are close to a normal distribution if possible.

Therefore we will pick Bedrooms, PropertyType and Town as our variables from our previous analysis. 

This is because there is no missing data for these variables, they are not correlated to each other and show a strong relationship in the previous plots. We also do not want to overfit by fitting on too many variables.

We can see below that most of our variables are statistically significant when we look at the T-statistic which is far from zero or the p-value which is very close to zero.

In [8]:
features = ['bedrooms', 'property_type', 'town']

formula = f'{predict_column} ~ ' + ' + '.join(features)
display(formula)

model = sm.ols(formula, data=clean_df)
reg = model.fit()

predicted_log_sale_price = reg.predict(clean_df)
mse = (predicted_log_sale_price - clean_df['log_sale_price']).pow(2).sum()

print(f'Mean Squared Error: {mse:.4f}')
print(reg.summary2())

'log_sale_price ~ bedrooms + property_type + town'

Mean Squared Error: 526.4590
                     Results: Ordinary least squares
Model:                 OLS                Adj. R-squared:       0.784    
Dependent Variable:    log_sale_price     AIC:                  1262.0761
Date:                  2019-05-06 00:54   BIC:                  1498.3413
No. Observations:      7700               Log-Likelihood:       -597.04  
Df Model:              33                 F-statistic:          848.2    
Df Residuals:          7666               Prob (F-statistic):   0.00     
R-squared:             0.785              Scale:                0.068675 
-------------------------------------------------------------------------
                          Coef.  Std.Err.    t     P>|t|   [0.025  0.975]
-------------------------------------------------------------------------
Intercept                12.9188   0.0224 576.4891 0.0000 12.8749 12.9627
property_type[T.House]    0.5703   0.0089  64.0066 0.0000  0.5529  0.5878
property_type[T.Terrace]  0.34

## Cross Validation

We see in the previous section that we are achieving an r-squared of 0.79. We need to check if the variables we have picked are robust if we split our dataset into smaller chunks and fit on one chunk and test on the rest of the dataset to check we get similar r-squared on the in sample and the validation set. We see below that our r-squared for both seem to stay consistent.

In [9]:
def cross_validate(formula, data, chunks=5):
    
    r2_list = []
    predicted_r2_list = []
    
    for _, df in data.groupby(np.arange(len(data)) // (len(data) // chunks)):
        
        model_temp = sm.ols(formula, data=df)
        reg_temp = model_temp.fit()
        
        other_data = data.loc[~data['property_id'].isin(df['property_id'])]
        other_data['predicted_log_sale_price'] = reg_temp.predict(other_data)
        
        SS_tot = (other_data['log_sale_price'] - other_data['log_sale_price'].mean()).pow(2).sum()
        SS_reg = (other_data['log_sale_price'] - other_data['predicted_log_sale_price']).pow(2).sum()
        
        r2_list.append(reg_temp.rsquared)
        predicted_r2_list.append(1 - SS_reg / SS_tot)
        
    return r2_list, predicted_r2_list

r2, predicted_r2 = cross_validate(formula=formula, data=clean_df, chunks=5)
print('R-squared for in sample set:')
display(r2)
print('R-squared for validation set:')
display(predicted_r2)

R-squared for in sample set:


[0.7881848723488568,
 0.7932874698735405,
 0.806929860146521,
 0.7771684269485334,
 0.7813298943862492]

R-squared for validation set:


[0.7783795157917937,
 0.7762270910934662,
 0.7715455760072258,
 0.7834239538947663,
 0.7798136825229199]

## Prediction on Test Set

We now use the test set to get the predictions below.

In [10]:
raw_test_df = get_data(test_data_path)
clean_test_df = clean_data(df=raw_test_df, 
                           rename_columns=rename_columns, 
                           category_columns=category_columns, 
                           log_columns=[new_predict_column])
display(clean_test_df.head())

clean_test_df['log_sale_price'] = reg.predict(clean_test_df)
iplot([go.Histogram(x=clean_test_df['log_sale_price'])])

clean_test_df['sale_price'] = np.exp(clean_test_df['log_sale_price'])
iplot([go.Histogram(x=clean_test_df['sale_price'])])

keep_rename_columns = {'property_id': 'PropertyID', 'sale_price': 'PredictedSalePrice'}
output_df = clean_test_df[list(keep_rename_columns.keys())].rename(columns=keep_rename_columns)
display(output_df.shape)
display(output_df.head())

output_df.to_csv(output_path)

No columns to fit.


property_id  sale_date         town  bedrooms  bathroom property_type  \
0         2739 2016-10-08      Malabar         4       1.0         House   
1          571 2016-08-13      Preston         4       1.0         House   
2         1311 2016-09-10  Carlingford         4       NaN         House   
3         7546 2017-10-21   Abbotsford         3       1.0         House   
4         1975 2016-08-06      Enfield         4       2.0         House   

   distance_from_cbd  car_spaces  garden_sqm  land_sqm  floor_sqm  year_built  \
0                5.5         1.0         NaN     314.0        NaN         NaN   
1               13.9         2.0       112.0     658.0      112.0         NaN   
2               11.4         NaN         NaN       NaN        NaN         NaN   
3                8.4         2.0         NaN       NaN        NaN         NaN   
4               13.0         4.0         NaN    1011.0        NaN         NaN   

  region  town_density  year  month year_month  
0  ZoneA       11364.0  2016     10 2016-10-31  
1  ZoneB       10969.0  2016      8 2016-08-31  
2  ZoneB        7822.0  2016      9 2016-09-30  
3  ZoneB        8801.0  2017     10 2017-10-31  
4  ZoneA        8870.0  2016      8 2016-08-31

(1924, 2)

PropertyID  PredictedSalePrice
0        2739        1.723765e+06
1         571        1.490260e+06
2        1311        1.654569e+06
3        7546        1.522357e+06
4        1975        9.269606e+05

## Further Work

- Look to formalise checking if a dataset has a normal distribution by checking for skewness and kurtosis.
- Look into filling in some of the missing data such as the sqm.
- Try fitting on less data by dropping the rows with missing data and comparing with the current model.
- Look into non linear to use some of the variables such as sqm where the relationship with house prices seem to flatten as it increases. This could be using neural networks but I think it would require more data points.